<a href="https://colab.research.google.com/github/mohammadbadi/Clustering_Frequency/blob/main/Code%20Sections/5.7%20Clustering%20Model%20Training.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### **5.7 Clustering Model Training**

In [ ]:
import warnings                                                                   # Import necessary libraries
import itertools
import numpy as np
import pandas as pd
import time
from sklearn.cluster import KMeans, DBSCAN
from sklearn.metrics import silhouette_score, davies_bouldin_score, calinski_harabasz_score
from sklearn.preprocessing import StandardScaler
from IPython.display import display, HTML

print("\n\n")
warnings.filterwarnings("ignore", category=DeprecationWarning)                    # Ignore Deprecation Warnings
warnings.filterwarnings("ignore", category=FutureWarning)                         # Ignore future warnings

features = [                                                                      # Define feature list
    'OCC_YEAR', 'OCC_DOY', 'OCC_HOUR', 'LONG_WGS84', 'LAT_WGS84',
    'OCC_Month_Encoded', 'OCC_DOW_Encoded', 'Hood_158_Encoded', 'Division_Encoded',
    'Location_Engineered_Other', 'Location_Engineered_Public', 'Location_Engineered_Residential'
]

all_combinations = [list(combo) for r in range(4, 8) for combo in itertools.combinations(features, r)]  # Generate feature combinations (sizes 4, 5, 6 and 7)

formatted_combinations_df = pd.DataFrame(all_combinations)                        # Save feature combinations to CSV
formatted_combinations_df.to_csv('Feature_Combo_Current.csv', index=False)
display(HTML("<p style='color: green; font-size:16px;'><b>Feature sets saved to 'Feature_Combo_Current.csv'</b></p>"))

url = "https://raw.githubusercontent.com/mohammadbadi/CrimeAnalytics_Clustering/refs/heads/main/Output_CSV/FE_Encoded.csv"  # Read the dataset from CSV file
data = pd.read_csv(url)

sample_data = data.sample(frac=0.1, random_state=42)                              # Sample 10% of the data for clustering
results = {}                                                                      # Track results - to store clustering metrics for each feature set
set_counters = {}                                                                 # To track counts per number of features
total_models = 0

def color_silhouette(value):                                                      # HTML helper functions for color coding Silhouette Score
    """Color code Silhouette Score (higher is better)"""
    if value >= 0.6:
        color = "#32cd32"                                                         # green
    elif value >= 0.3:
        color = "#ffcc00"                                                         # yellow
    else:
        color = "#ff6347"                                                         # red
    return f"<span style='color: {color}; font-weight: bold;'>{value:.2f}</span>"

def color_dbi(value):                                                             # HTML helper functions for color coding DB index
    """Color code Davies-Bouldin Index (lower is better)"""
    if value <= 1.0:
        color = "#32cd32"                                                         # green
    elif value <= 1.5:
        color = "#ffcc00"                                                         # yellow
    else:
        color = "#ff6347"                                                         # red
    return f"<span style='color: {color}; font-weight: bold;'>{value:.2f}</span>"

def color_accuracy(value):                                                        # HTML helper functions for color coding Accuracy Percentage Score
    """Color code prediction accuracy: below 50% red, 50.1%+ green"""
    if value < 50.1:
        color = "#ff6347"                                                         # red
    else:
        color = "#32cd32"                                                         # green
    return f"<span style='color: {color}; font-weight: bold;'>{value:.2f}%</span>"

for i, feature_set in enumerate(all_combinations):                                # Iterate through feature sets
    total_models += 1
    valid_features = [f for f in feature_set if f in sample_data.columns]         # Select valid features (ensuring they exist in the dataset)
    if len(valid_features) != len(feature_set):
        print(f"Warning: Some features in {feature_set} are missing. Using only: {valid_features}")
    data_for_clustering = sample_data[valid_features]
    numerical_cols = data_for_clustering.select_dtypes(include=['int64', 'float64']).columns.tolist()     # Standardize numerical columns
    scaler = StandardScaler()
    data_scaled = pd.DataFrame(scaler.fit_transform(data_for_clustering[numerical_cols]), columns=numerical_cols)
    categorical_cols = [col for col in valid_features if col not in numerical_cols]       # Append any categorical columns
    if categorical_cols:
        data_scaled = pd.concat([data_scaled, data_for_clustering[categorical_cols]], axis=1)
    kmeans = KMeans(n_clusters=4, random_state=42)                                # Perform KMeans clustering
    kmeans_labels = kmeans.fit_predict(data_scaled)
    dbscan = DBSCAN(eps=0.5, min_samples=5)                                       # DBSCAN Clustering
    dbscan_labels = dbscan.fit_predict(data_scaled)

    silhouette_kmeans = silhouette_score(data_scaled, kmeans_labels)              # Calculate KMeans metrics
    dbi_kmeans = davies_bouldin_score(data_scaled, kmeans_labels)
    ch_kmeans = calinski_harabasz_score(data_scaled, kmeans_labels)
    kmeans_accuracy = max(0, silhouette_kmeans) * 100

    silhouette_dbscan = -1 if len(set(dbscan_labels)) <= 1 else silhouette_score(data_scaled, dbscan_labels)     # Calculate DBSCAN metrics
    dbi_dbscan = -1 if len(set(dbscan_labels)) <= 1 else davies_bouldin_score(data_scaled, dbscan_labels)
    dbscan_accuracy = max(0, silhouette_dbscan) * 100

    num_features = len(valid_features)                                            # Update set_counters
    if num_features not in set_counters:
        set_counters[num_features] = 0
    set_counters[num_features] += 1
    set_number = set_counters[num_features]

    formatted_features = [f"'{feature}'" for feature in valid_features]           # Format features string
    feature_names_string = f"[{', '.join(formatted_features)}]"

    results[tuple(valid_features)] = {                                            # Store results in dictionary
        'Feature Set': f"{num_features}_Set_{set_number}",
        'Number of Features': num_features,
        'KMeans Silhouette Score': silhouette_kmeans,
        'KMeans Davies-Bouldin Index': dbi_kmeans,
        'KMeans Calinski-Harabasz Score': ch_kmeans,
        'KMeans Prediction Accuracy': kmeans_accuracy,
        'DBSCAN Silhouette Score': silhouette_dbscan,
        'DBSCAN Davies-Bouldin Index': dbi_dbscan,
        'DBSCAN Prediction Accuracy': dbscan_accuracy,
        'Feature_Names_String': feature_names_string
    }

                                                                                  # Create HTML table output for current result
    results_html = f"""
    <div style="margin: 10px auto; width: 80%; border: 2px solid #ddd; padding: 10px; background-color: #f9f9f9;">
      <table style="width: 100%; border-collapse: collapse; text-align: center;">
        <tr>
          <th colspan="3" style="font-size: 14px; padding: 10px; text-align: left;">Result of Feature Set {num_features}_Set_{set_number}</th>
        </tr>
        <tr>
          <th colspan="3" style="font-size: 13px; padding: 5px; text-align: left;">Features : {feature_names_string}</th>
        </tr>
        <tr style="background-color: #e0e0e0; font-weight: bold;">
          <td style="padding: 8px; border: 1px solid #ddd;">Statistic</td>
          <td style="padding: 8px; border: 1px solid #ddd;">KMeans</td>
          <td style="padding: 8px; border: 1px solid #ddd;">DBSCAN</td>
        </tr>
        <tr>
          <td style="padding: 8px; border: 1px solid #ddd;">Silhouette Score</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{color_silhouette(silhouette_kmeans)}</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{"N/A" if silhouette_dbscan == -1 else color_silhouette(silhouette_dbscan)}</td>
        </tr>
        <tr>
          <td style="padding: 8px; border: 1px solid #ddd;">Davies-Bouldin Index</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{color_dbi(dbi_kmeans)}</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{"N/A" if dbi_dbscan == -1 else color_dbi(dbi_dbscan)}</td>
        </tr>
        <tr>
          <td style="padding: 8px; border: 1px solid #ddd;">Calinski-Harabasz Score</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{round(ch_kmeans,2)}</td>
          <td style="padding: 8px; border: 1px solid #ddd;">-</td>
        </tr>
        <tr style="font-weight: bold;">
          <td style="padding: 8px; border: 1px solid #ddd;">Prediction Accuracy</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{color_accuracy(kmeans_accuracy)}</td>
          <td style="padding: 8px; border: 1px solid #ddd;">{color_accuracy(dbscan_accuracy)}</td>
        </tr>
      </table>
    </div>
    """
    display(HTML(results_html))
    time.sleep(0.1)

results_df = pd.DataFrame(results.values())                                         # Convert results to DataFrame
results_df.to_csv('Feature_Combo_Current_Results.csv', index=False)                 # Save the dataframe as CSV File
files.download('Feature_Combo_Current_Results.csv')                                 # Download the CSV file
                                                                                    # Display formatted message for saved file
display(HTML("""
    <p style="color: darkblue; font-size: 18px; font-weight: bold;">
         Results have been saved as <span style="color: green;">Feature_Combo_Current_Results.csv</span>.
    </p>
"""))
display(HTML(f"<h2 style='color: navy; font-size:18px;'><b>Total K-Means & DBSCAN Clustering Models Trained: {total_models}</b></h2>")) # Display total models trained
print("\n\n")
                                                                                    # Final summary display
display(HTML(f"""
<div style="font-family: Arial, sans-serif; font-size: 18px; padding: 15px; border-radius: 10px;
             background: #282c34; color: #61dafb; text-align: center; width: 60%; margin: 20px auto;
             box-shadow: 2px 2px 10px rgba(0,0,0,0.2);">
    <strong>Total K-Means & DBSCAN Clustering models trained:</strong>
    <span style="color: #ffcc00; font-size: 22px;">{total_models}</span>
</div>
"""))